Credit: https://towardsdatascience.com/using-python-to-create-a-world-map-from-a-list-of-country-names-cd7480d03b10

In [1]:
import pandas as pd
import numpy as np
import igraph as ig
import collections
import matplotlib
from pycountry_convert import country_alpha2_to_continent_code, country_name_to_country_alpha2
from geopy.geocoders import Nominatim
import folium
from folium.plugins import MarkerCluster
import json
%matplotlib inline

In [2]:
df_spinglass = pd.read_csv('df_spinglass_undirected_no_inter.csv')
df_spinglass

Unnamed: 0                    name  community
0             0                 Albania          1
1             1                 Bahamas          1
2             2                 Algeria          6
3             3  British Virgin Islands          6
4             4          United Kingdom          6
..          ...                     ...        ...
190         190               Venezuela          1
191         191                 Vietnam          6
192         192                   Yemen          1
193         193                  Zambia          6
194         194                Zimbabwe          6

[195 rows x 3 columns]

In [3]:
df_walktrap = pd.read_csv('df_walktrap_undirected_no_inter.csv')
df_walktrap

Unnamed: 0                    name  community
0             0                 Albania          0
1             1                 Bahamas          1
2             2                 Algeria          2
3             3  British Virgin Islands          1
4             4          United Kingdom          1
..          ...                     ...        ...
190         190               Venezuela          1
191         191                 Vietnam          1
192         192                   Yemen         63
193         193                  Zambia         64
194         194                Zimbabwe         65

[195 rows x 3 columns]

In [4]:
df_leading_eigen = pd.read_csv('df_leading_eigen_undirected_no_inter.csv')
df_leading_eigen

Unnamed: 0                    name  community
0             0                 Albania          0
1             1                 Bahamas          0
2             2                 Algeria          1
3             3  British Virgin Islands          1
4             4          United Kingdom          1
..          ...                     ...        ...
190         190               Venezuela          0
191         191                 Vietnam          1
192         192                   Yemen          0
193         193                  Zambia          1
194         194                Zimbabwe          1

[195 rows x 3 columns]

In [5]:
df_louvain = pd.read_csv('df_louvain_undirected_no_inter.csv')
df_louvain

Unnamed: 0                    name  community
0             0                 Albania          0
1             1                 Bahamas          0
2             2                 Algeria          1
3             3  British Virgin Islands          1
4             4          United Kingdom          1
..          ...                     ...        ...
190         190               Venezuela          0
191         191                 Vietnam          1
192         192                   Yemen          0
193         193                  Zambia          1
194         194                Zimbabwe          1

[195 rows x 3 columns]

In [6]:
df_leiden = pd.read_csv('df_leiden_undirected_no_inter.csv')
df_leiden

Unnamed: 0                    name  community
0             0                 Albania          0
1             1                 Bahamas          1
2             2                 Algeria          2
3             3  British Virgin Islands          1
4             4          United Kingdom          1
..          ...                     ...        ...
190         190               Venezuela          1
191         191                 Vietnam          1
192         192                   Yemen         93
193         193                  Zambia         94
194         194                Zimbabwe         95

[195 rows x 3 columns]

In [7]:
df_fastgreedy = pd.read_csv('df_fastgreedy_undirected_no_inter.csv')
df_fastgreedy

Unnamed: 0                    name  community
0             0                 Albania          0
1             1                 Bahamas          0
2             2                 Algeria          1
3             3  British Virgin Islands          1
4             4          United Kingdom          1
..          ...                     ...        ...
190         190               Venezuela          0
191         191                 Vietnam          1
192         192                   Yemen          0
193         193                  Zambia          1
194         194                Zimbabwe          1

[195 rows x 3 columns]

In [8]:
df_infomap = pd.read_csv('df_infomap_undirected_no_inter.csv')
df_infomap

Unnamed: 0                    name  community
0             0                 Albania          0
1             1                 Bahamas          0
2             2                 Algeria          0
3             3  British Virgin Islands          0
4             4          United Kingdom          0
..          ...                     ...        ...
190         190               Venezuela          0
191         191                 Vietnam          0
192         192                   Yemen          0
193         193                  Zambia          0
194         194                Zimbabwe          0

[195 rows x 3 columns]

In [9]:
def get_continent(col):
    try:
        cn_a2_code =  country_name_to_country_alpha2(col)
    except:
        cn_a2_code = 'Unknown' 
    try:
        cn_continent = country_alpha2_to_continent_code(cn_a2_code)
    except:
        cn_continent = 'Unknown' 
    return (cn_a2_code, cn_continent)

In [10]:

df_spinglass['codes'] = df_spinglass['name'].apply(get_continent)
df_spinglass['country_code'] = df_spinglass['codes'].apply(lambda x: x[0])
df_spinglass['continent_code'] = df_spinglass['codes'].apply(lambda x: x[1])

df_walktrap['codes'] = df_walktrap['name'].apply(get_continent)
df_walktrap['country_code'] = df_walktrap['codes'].apply(lambda x: x[0])
df_walktrap['continent_code'] = df_walktrap['codes'].apply(lambda x: x[1])

df_leading_eigen['codes'] = df_leading_eigen['name'].apply(get_continent)
df_leading_eigen['country_code'] = df_leading_eigen['codes'].apply(lambda x: x[0])
df_leading_eigen['continent_code'] = df_leading_eigen['codes'].apply(lambda x: x[1])

df_fastgreedy['codes'] = df_fastgreedy['name'].apply(get_continent)
df_fastgreedy['country_code'] = df_fastgreedy['codes'].apply(lambda x: x[0])
df_fastgreedy['continent_code'] = df_fastgreedy['codes'].apply(lambda x: x[1])

df_leiden['codes'] = df_leiden['name'].apply(get_continent)
df_leiden['country_code'] = df_leiden['codes'].apply(lambda x: x[0])
df_leiden['continent_code'] = df_leiden['codes'].apply(lambda x: x[1])

df_louvain['codes'] = df_louvain['name'].apply(get_continent)
df_louvain['country_code'] = df_louvain['codes'].apply(lambda x: x[0])
df_louvain['continent_code'] = df_louvain['codes'].apply(lambda x: x[1])

df_infomap['codes'] = df_infomap['name'].apply(get_continent)
df_infomap['country_code'] = df_infomap['codes'].apply(lambda x: x[0])
df_infomap['continent_code'] = df_infomap['codes'].apply(lambda x: x[1])

df_spinglass
#df_walktrap
#df_infomap

Unnamed: 0                    name  community     codes country_code  \
0             0                 Albania          1  (AL, EU)           AL   
1             1                 Bahamas          1  (BS, NA)           BS   
2             2                 Algeria          6  (DZ, AF)           DZ   
3             3  British Virgin Islands          6  (VG, NA)           VG   
4             4          United Kingdom          6  (GB, EU)           GB   
..          ...                     ...        ...       ...          ...   
190         190               Venezuela          1  (VE, SA)           VE   
191         191                 Vietnam          6  (VN, AS)           VN   
192         192                   Yemen          1  (YE, AS)           YE   
193         193                  Zambia          6  (ZM, AF)           ZM   
194         194                Zimbabwe          6  (ZW, AF)           ZW   

    continent_code  
0               EU  
1               NA  
2               AF  
3               NA  
4               EU  
..             ...  
190             SA  
191             AS  
192             AS  
193             AF  
194             AF  

[195 rows x 6 columns]

In [11]:
df_countries = df_spinglass[['name','country_code']]
df_countries

name country_code
0                   Albania           AL
1                   Bahamas           BS
2                   Algeria           DZ
3    British Virgin Islands           VG
4            United Kingdom           GB
..                      ...          ...
190               Venezuela           VE
191                 Vietnam           VN
192                   Yemen           YE
193                  Zambia           ZM
194                Zimbabwe           ZW

[195 rows x 2 columns]

In [12]:
def geolocate(country,country_code):
    geolocator = Nominatim(user_agent = country)
    try:
        # Geolocate the center of the country
        loc = geolocator.geocode(country, country_codes = country_code)
        # And return latitude and longitude
        return (round(loc.latitude,2), round(loc.longitude,2))
    except:
        # Return missing value
        loc = geolocator.geocode(country, country_codes = None)
        return (round(loc.latitude,2), round(loc.longitude,2))

In [13]:
df_countries['Lat_Long'] = df_countries.apply(lambda x: geolocate(x['name'], x['country_code']),axis = 1)

<ipython-input-13-a7c0add9ac3a>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_countries['Lat_Long'] = df_countries.apply(lambda x: geolocate(x['name'], x['country_code']),axis = 1)


In [14]:
df_countries['Latitude'] = df_countries['Lat_Long'].apply(lambda x: x[0]) # there is a really annnoying error here when there shouldnt be, for some reason it cant  look at the first and seocnd index of the tuplet
df_countries['Longitude'] = df_countries['Lat_Long'].apply(lambda x: x[1])

df_spinglass = df_spinglass.merge(df_countries, how = 'left')
df_walktrap = df_walktrap.merge(df_countries, how = 'left')
df_fastgreedy = df_fastgreedy.merge(df_countries,how = 'left')
df_leiden = df_leiden.merge(df_countries,how = 'left')
df_louvain = df_louvain.merge(df_countries,how = 'left')
df_leading_eigen = df_leading_eigen.merge(df_countries,how = 'left')
df_infomap = df_infomap.merge(df_countries,how = 'left')
df_walktrap

<ipython-input-14-3bd20985f6ec>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_countries['Latitude'] = df_countries['Lat_Long'].apply(lambda x: x[0]) # there is a really annnoying error here when there shouldnt be, for some reason it cant  look at the first and seocnd index of the tuplet
<ipython-input-14-3bd20985f6ec>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_countries['Longitude'] = df_countries['Lat_Long'].apply(lambda x: x[1])


Unnamed: 0                    name  community     codes country_code  \
0             0                 Albania          0  (AL, EU)           AL   
1             1                 Bahamas          1  (BS, NA)           BS   
2             2                 Algeria          2  (DZ, AF)           DZ   
3             3  British Virgin Islands          1  (VG, NA)           VG   
4             4          United Kingdom          1  (GB, EU)           GB   
..          ...                     ...        ...       ...          ...   
190         190               Venezuela          1  (VE, SA)           VE   
191         191                 Vietnam          1  (VN, AS)           VN   
192         192                   Yemen         63  (YE, AS)           YE   
193         193                  Zambia         64  (ZM, AF)           ZM   
194         194                Zimbabwe         65  (ZW, AF)           ZW   

    continent_code         Lat_Long  Latitude  Longitude  
0               EU     (41.0, 20.0)     41.00      20.00  
1               NA   (24.77, -78.0)     24.77     -78.00  
2               AF      (28.0, 3.0)     28.00       3.00  
3               NA   (18.4, -64.57)     18.40     -64.57  
4               EU    (54.7, -3.28)     54.70      -3.28  
..             ...              ...       ...        ...  
190             SA    (8.0, -66.11)      8.00     -66.11  
191             AS  (13.29, 108.43)     13.29     108.43  
192             AS   (16.35, 47.89)     16.35      47.89  
193             AF  (-14.52, 27.56)    -14.52      27.56  
194             AF  (-18.46, 29.75)    -18.46      29.75  

[195 rows x 9 columns]

In [15]:
df_spinglass.dropna(inplace = True)
df_spinglass.reset_index(drop = True, inplace = True)

df_walktrap.dropna(inplace = True)
df_walktrap.reset_index(drop = True, inplace = True)

df_louvain.dropna(inplace = True)
df_louvain.reset_index(drop = True, inplace = True)

df_leiden.dropna(inplace = True)
df_leiden.reset_index(drop = True, inplace = True)

df_leading_eigen.dropna(inplace = True)
df_leading_eigen.reset_index(drop = True, inplace = True)

df_fastgreedy.dropna(inplace = True)
df_fastgreedy.reset_index(drop = True, inplace = True)

df_infomap.dropna(inplace = True)
df_infomap.reset_index(drop = True, inplace = True)


df_spinglass

Unnamed: 0                    name  community     codes country_code  \
0             0                 Albania          1  (AL, EU)           AL   
1             1                 Bahamas          1  (BS, NA)           BS   
2             2                 Algeria          6  (DZ, AF)           DZ   
3             3  British Virgin Islands          6  (VG, NA)           VG   
4             4          United Kingdom          6  (GB, EU)           GB   
..          ...                     ...        ...       ...          ...   
190         190               Venezuela          1  (VE, SA)           VE   
191         191                 Vietnam          6  (VN, AS)           VN   
192         192                   Yemen          1  (YE, AS)           YE   
193         193                  Zambia          6  (ZM, AF)           ZM   
194         194                Zimbabwe          6  (ZW, AF)           ZW   

    continent_code         Lat_Long  Latitude  Longitude  
0               EU     (41.0, 20.0)     41.00      20.00  
1               NA   (24.77, -78.0)     24.77     -78.00  
2               AF      (28.0, 3.0)     28.00       3.00  
3               NA   (18.4, -64.57)     18.40     -64.57  
4               EU    (54.7, -3.28)     54.70      -3.28  
..             ...              ...       ...        ...  
190             SA    (8.0, -66.11)      8.00     -66.11  
191             AS  (13.29, 108.43)     13.29     108.43  
192             AS   (16.35, 47.89)     16.35      47.89  
193             AF  (-14.52, 27.56)    -14.52      27.56  
194             AF  (-18.46, 29.75)    -18.46      29.75  

[195 rows x 9 columns]

In [16]:
df_spinglass['Latitude'] = df_spinglass['Lat_Long'].apply(lambda x: x[0])
df_spinglass['Longitude'] = df_spinglass['Lat_Long'].apply(lambda x: x[1])

df_walktrap['Latitude'] = df_walktrap['Lat_Long'].apply(lambda x: x[0])
df_walktrap['Longitude'] = df_walktrap['Lat_Long'].apply(lambda x: x[1])

df_louvain['Latitude'] = df_louvain['Lat_Long'].apply(lambda x: x[0])
df_louvain['Longitude'] = df_louvain['Lat_Long'].apply(lambda x: x[1])

df_leiden['Latitude'] = df_leiden['Lat_Long'].apply(lambda x: x[0])
df_leiden['Longitude'] = df_leiden['Lat_Long'].apply(lambda x: x[1])

df_leading_eigen['Latitude'] = df_leading_eigen['Lat_Long'].apply(lambda x: x[0])
df_leading_eigen['Longitude'] = df_leading_eigen['Lat_Long'].apply(lambda x: x[1])

df_fastgreedy['Latitude'] = df_fastgreedy['Lat_Long'].apply(lambda x: x[0])
df_fastgreedy['Longitude'] = df_fastgreedy['Lat_Long'].apply(lambda x: x[1])

df_infomap['Latitude'] = df_infomap['Lat_Long'].apply(lambda x: x[0])
df_infomap['Longitude'] = df_infomap['Lat_Long'].apply(lambda x: x[1])

df_spinglass

Unnamed: 0                    name  community     codes country_code  \
0             0                 Albania          1  (AL, EU)           AL   
1             1                 Bahamas          1  (BS, NA)           BS   
2             2                 Algeria          6  (DZ, AF)           DZ   
3             3  British Virgin Islands          6  (VG, NA)           VG   
4             4          United Kingdom          6  (GB, EU)           GB   
..          ...                     ...        ...       ...          ...   
190         190               Venezuela          1  (VE, SA)           VE   
191         191                 Vietnam          6  (VN, AS)           VN   
192         192                   Yemen          1  (YE, AS)           YE   
193         193                  Zambia          6  (ZM, AF)           ZM   
194         194                Zimbabwe          6  (ZW, AF)           ZW   

    continent_code         Lat_Long  Latitude  Longitude  
0               EU     (41.0, 20.0)     41.00      20.00  
1               NA   (24.77, -78.0)     24.77     -78.00  
2               AF      (28.0, 3.0)     28.00       3.00  
3               NA   (18.4, -64.57)     18.40     -64.57  
4               EU    (54.7, -3.28)     54.70      -3.28  
..             ...              ...       ...        ...  
190             SA    (8.0, -66.11)      8.00     -66.11  
191             AS  (13.29, 108.43)     13.29     108.43  
192             AS   (16.35, 47.89)     16.35      47.89  
193             AF  (-14.52, 27.56)    -14.52      27.56  
194             AF  (-18.46, 29.75)    -18.46      29.75  

[195 rows x 9 columns]

In [17]:
df_spinglass['community'].value_counts()

6    83
1    46
5    38
3    23
4     2
0     2
2     1
Name: community, dtype: int64

In [18]:
df_leiden['community'].value_counts()

1     100
95      1
35      1
26      1
27      1
     ... 
66      1
67      1
68      1
69      1
0       1
Name: community, Length: 96, dtype: int64

In [19]:
df_fastgreedy['community'].value_counts()

1    85
0    60
2    40
3     6
5     2
4     2
Name: community, dtype: int64

## Let's map the community for Spinglass

In [20]:
#Setting up the world countries data URL
url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
country_shapes = f'{url}/world-countries.json'

In [21]:
#empty map
world_map_spinglass = folium.Map(tiles="cartodbpositron")
marker_cluster_spinglass = MarkerCluster().add_to(world_map_spinglass)
#for each coordinate, create circlemarker of user percent
for i in range(len(df_spinglass)):
        lat = df_spinglass.iloc[i]['Latitude']
        long = df_spinglass.iloc[i]['Longitude']
        radius=5
        popup_text = """Country : {}<br>
                    Community : {}<br>"""
        popup_text = popup_text.format(df_spinglass.iloc[i]['name'],
                                   df_spinglass.iloc[i]['community']
                                   )
        folium.CircleMarker(location = [lat, long], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster_spinglass)

folium.Choropleth(
    #The GeoJSON data to represent the world country
    geo_data=country_shapes,
    name='Spinglass Community Choropleth',
    data=df_spinglass,
    #The column aceppting list with 2 value; The country name and  the numerical value
    columns=['name',"community"],
    key_on='feature.properties.name',
    fill_color='Set1',
    nan_fill_color='white',
    legend_name = 'Community'
).add_to(world_map_spinglass)
world_map_spinglass

## Walktrap

In [22]:
#empty map
world_map_walktrap = folium.Map(tiles="cartodbpositron")
marker_cluster_walktrap = MarkerCluster().add_to(world_map_walktrap)
#for each coordinate, create circlemarker of user percent
for i in range(len(df_walktrap)):
        lat = df_walktrap.iloc[i]['Latitude']
        long = df_walktrap.iloc[i]['Longitude']
        radius=5
        popup_text = """Country : {}<br>
                    Community : {}<br>"""
        popup_text = popup_text.format(df_walktrap.iloc[i]['name'],
                                   df_walktrap.iloc[i]['community']
                                   )
        folium.CircleMarker(location = [lat, long], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster_walktrap)

folium.Choropleth(
    #The GeoJSON data to represent the world country
    geo_data=country_shapes,
    name='Walktrap Community Choropleth',
    data=df_walktrap,
    #The column aceppting list with 2 value; The country name and  the numerical value
    columns=['name',"community"],
    key_on='feature.properties.name',
    fill_color='Set1',
    nan_fill_color='white',
    legend_name = 'Community'
).add_to(world_map_walktrap)
world_map_walktrap

## Louvain

In [23]:
#empty map
world_map_louvain = folium.Map(tiles="cartodbpositron")
marker_cluster_louvain = MarkerCluster().add_to(world_map_louvain)
#for each coordinate, create circlemarker of user percent
for i in range(len(df_louvain)):
        lat = df_louvain.iloc[i]['Latitude']
        long = df_louvain.iloc[i]['Longitude']
        radius=5
        popup_text = """Country : {}<br>
                    Community : {}<br>"""
        popup_text = popup_text.format(df_louvain.iloc[i]['name'],
                                   df_louvain.iloc[i]['community']
                                   )
        folium.CircleMarker(location = [lat, long], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster_louvain)

folium.Choropleth(
    #The GeoJSON data to represent the world country
    geo_data=country_shapes,
    name='Infomap Community Choropleth',
    data=df_louvain,
    #The column aceppting list with 2 value; The country name and  the numerical value
    columns=['name',"community"],
    key_on='feature.properties.name',
    fill_color='Set1',
    nan_fill_color='white',
    legend_name = 'Community'
).add_to(world_map_louvain)
world_map_louvain

## Leiden

In [24]:
#empty map
world_map_leiden = folium.Map(tiles="cartodbpositron")
marker_cluster_leiden = MarkerCluster().add_to(world_map_leiden)
#for each coordinate, create circlemarker of user percent
for i in range(len(df_leiden)):
        lat = df_leiden.iloc[i]['Latitude']
        long = df_leiden.iloc[i]['Longitude']
        radius=5
        popup_text = """Country : {}<br>
                    Community : {}<br>"""
        popup_text = popup_text.format(df_leiden.iloc[i]['name'],
                                   df_leiden.iloc[i]['community']
                                   )
        folium.CircleMarker(location = [lat, long], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster_leiden)

folium.Choropleth(
    #The GeoJSON data to represent the world country
    geo_data=country_shapes,
    name='Infomap Community Choropleth',
    data=df_leiden,
    #The column aceppting list with 2 value; The country name and  the numerical value
    columns=['name',"community"],
    key_on='feature.properties.name',
    fill_color='Set1',
    nan_fill_color='white',
    legend_name = 'Community'
).add_to(world_map_leiden)
world_map_leiden

## Leading Eigen

In [25]:
#empty map
world_map_leading_eigen = folium.Map(tiles="cartodbpositron")
marker_cluster_leading_eigen = MarkerCluster().add_to(world_map_leading_eigen)
#for each coordinate, create circlemarker of user percent
for i in range(len(df_leading_eigen)):
        lat = df_leading_eigen.iloc[i]['Latitude']
        long = df_leading_eigen.iloc[i]['Longitude']
        radius=5
        popup_text = """Country : {}<br>
                    Community : {}<br>"""
        popup_text = popup_text.format(df_leading_eigen.iloc[i]['name'],
                                   df_leading_eigen.iloc[i]['community']
                                   )
        folium.CircleMarker(location = [lat, long], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster_leading_eigen)

folium.Choropleth(
    #The GeoJSON data to represent the world country
    geo_data=country_shapes,
    name='Infomap Community Choropleth',
    data=df_leading_eigen,
    #The column aceppting list with 2 value; The country name and  the numerical value
    columns=['name',"community"],
    key_on='feature.properties.name',
    fill_color='Set1',
    nan_fill_color='white',
    legend_name = 'Community'
).add_to(world_map_leading_eigen)
world_map_leading_eigen

## Fastgreedy

In [26]:
#empty map
world_map_fastgreedy = folium.Map(tiles="cartodbpositron")
marker_cluster_fastgreedy = MarkerCluster().add_to(world_map_fastgreedy)
#for each coordinate, create circlemarker of user percent
for i in range(len(df_fastgreedy)):
        lat = df_leading_eigen.iloc[i]['Latitude']
        long = df_leading_eigen.iloc[i]['Longitude']
        radius=5
        popup_text = """Country : {}<br>
                    Community : {}<br>"""
        popup_text = popup_text.format(df_fastgreedy.iloc[i]['name'],
                                   df_fastgreedy.iloc[i]['community']
                                   )
        folium.CircleMarker(location = [lat, long], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster_fastgreedy)

folium.Choropleth(
    #The GeoJSON data to represent the world country
    geo_data=country_shapes,
    name='Fastgreedy Community Choropleth',
    data=df_fastgreedy,
    #The column aceppting list with 2 value; The country name and  the numerical value
    columns=['name',"community"],
    key_on='feature.properties.name',
    fill_color='Set1',
    nan_fill_color='white',
    legend_name = 'Community'
).add_to(world_map_fastgreedy)
world_map_fastgreedy

## Infomap

In [27]:
#empty map
world_map_infomap = folium.Map(tiles="cartodbpositron")
marker_cluster_infomap = MarkerCluster().add_to(world_map_infomap)
#for each coordinate, create circlemarker of user percent
for i in range(len(df_infomap)):
        lat = df_infomap.iloc[i]['Latitude']
        long = df_infomap.iloc[i]['Longitude']
        radius=5
        popup_text = """Country : {}<br>
                    Community : {}<br>"""
        popup_text = popup_text.format(df_infomap.iloc[i]['name'],
                                   df_infomap.iloc[i]['community']
                                   )
        folium.CircleMarker(location = [lat, long], radius=radius, popup= popup_text, fill =True).add_to(marker_cluster_infomap)

folium.Choropleth(
    #The GeoJSON data to represent the world country
    geo_data=country_shapes,
    name='Infomap Community Choropleth',
    data=df_infomap,
    #The column aceppting list with 2 value; The country name and  the numerical value
    columns=['name',"community"],
    key_on='feature.properties.name',
    fill_color='Set1',
    nan_fill_color='white',
    legend_name = 'Community'
).add_to(world_map_infomap)
world_map_infomap